## Movie Revenue Prediction

### Objective: Merge Feature Engineering Dataframe with movies_df to create movies_ml

In [1]:
%load_ext watermark
%watermark -a "Emily Schoof" -d -t -v -p numpy,pandas,matplotlib,sklearn,nltk

Emily Schoof 2019-08-20 15:40:19 

CPython 3.7.3
IPython 7.4.0

numpy 1.16.2
pandas 0.24.2
matplotlib 3.0.3
sklearn 0.20.3
nltk 3.4


In [2]:
# Load the dataset
%store -r movie_df_unnested
movie_df_unnested.shape

(4641, 10)

In [3]:
movie_df_unnested.head(2)

title       revenue                                    genres  \
0   Avatar  2.787965e+09  Action Adventure Fantasy Science Fiction   
1  Titanic  1.845034e+09                    Drama Romance Thriller   

                                            keywords original_language  \
0    culture clash   future   space war   space c...                en   
1    shipwreck   iceberg   ship   panic   titanic...                en   

                                production_companies  \
0  Ingenious Film Partners Twentieth Century Fox ...   
1  Paramount Pictures Twentieth Century Fox Film ...   

                         production_countries  runtime  \
0  US United States America GB United Kingdom    162.0   
1                    US United States America    194.0   

                spoken_languages  release_date  
0                   English Espa      20091210  
1  English Fran Deutsch Italiano      19971118

# Model Selection:  Linear and Ridge Regressions

### Target Variable: Movie Revenue *movie_df_unnested['revenue']*

## Create a Step-by-Step Pipeline

In [5]:
# Import necessary modules
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

# Import preprocessing modules
import spacy
from nltk.corpus import stopwords
from sklearn.impute import SimpleImputer # *Numerical* fill in missing values
from sklearn.preprocessing import FunctionTransformer, MaxAbsScaler # Isolate relevant features
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import CountVectorizer # Reduce dimensionality via creating hash values from text
from sklearn.feature_selection import chi2, SelectKBest # Dimensionality reduction techniue 

# Import pipeline components
#from sklearn.pipeline import Pipeline
#from sklearn.pipeline import FeatureUnion # streamline preprocessing steps when multiple datatypes are involved

# Import relevant classifiers
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge

# Import metrics modules
from sklearn.metrics import classification_report, confusion_matrix, roc_curve, roc_auc_score

### Define Target and Feature Variables

In [6]:
# Import relevent modules
from sklearn.model_selection import train_test_split, GridSearchCV

In [7]:
# Set up the target variable
y_target = movie_df_unnested['revenue'].values
print('Target: ', y_target.shape)

# Set the feature variables
X_features = movie_df_unnested.drop(columns=['revenue'], axis = 1)
feature_list = X_features.columns
print('Features: ', X_features.shape)

Target:  (4641,)
Features:  (4641, 9)


### Preprocessing Data

In [8]:
# Import relevant modules
from sklearn.feature_extraction.text import HashingVectorizer

In [10]:
movie_df_unnested.dtypes

title                    object
revenue                 float64
genres                   object
keywords                 object
original_language        object
production_companies     object
production_countries     object
runtime                 float64
spoken_languages         object
release_date              int64
dtype: object

**Text Columns**

In [11]:
def combine_text_columns(df):
    """ Convert All Values in a Column Into One Vector """
    
    # Replace nulls with empty spaces
    df.fillna('', inplace=True)
    
          # Join all columns into unique vectors
    return df.apply(lambda col: ' '.join(col), axis=1)

In [13]:
text_columns = ['title', 'genres', 'keywords', 'production_companies',
                'production_countries', 'spoken_languages']

token_alphanumeric = '[A-Za-z0-9]+(?=\\s+)'

X_feature_text = X_features[text_columns]

X_feature_text_vector = combine_text_columns(X_feature_text)

/anaconda3/lib/python3.7/site-packages/pandas/core/frame.py:4034: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  downcast=downcast, **kwargs)


In [14]:
# Create a vectorizer instance
hvectorizer = HashingVectorizer(binary=False, token_pattern=token_alphanumeric)

# build the vocabulary and convert text to a bag of words
X_features_text_transformed = hvectorizer.fit_transform(X_feature_text_vector)

In [15]:
X_features_text_transformed.shape

(4641, 1048576)

In [14]:
# Bag of Words (second round)

**Numerical Values**

In [16]:
numberic_columns = ['runtime', 'release_date']

X_feature_numberic = X_features[numberic_columns]

In [17]:
X_feature_numberic.shape

(4641, 2)

**Combine Processed Text and Numerical Features**

In [18]:
# Import Necessary Modules
from scipy.sparse import hstack

In [19]:
X_features_processed = hstack((X_features_text_transformed, np.array(X_feature_numberic))).toarray()

In [20]:
X_features_processed.shape

(4641, 1048578)

*Observations*: Over 1 million columns is a extraordinarily high dimensional dataset. Since purley running any model on this dataset would be time-intensive, a dimensionality reduction method needs to be applied. Singular Value Decomposition (SVD) is popular in the field of natural language processing to achieve a representation of the gigantic while sparse word frequency matrices.

### Apply SVD to X_features

### Split Data

In [21]:
# Create train and test data sets -> Arbitrary Random State of 42 Set with test/train size of 30/70 (>25% of data)
X_train, X_test, y_train, y_test = train_test_split(X_features_processed, y_target, test_size=0.3, random_state=42)
print(len(X_train), len(X_test), len(y_train), len(y_test))
X_train.shape, X_test.shape, y_train.shape, y_test.shape 

3248 1393 3248 1393


((3248, 1048578), (1393, 1048578), (3248,), (1393,))

## Run initial (simple) model

In [22]:
# Import relevent classifiers
from sklearn.linear_model import LinearRegression

In [ ]:
# Create a linear regression instance
lr = LinearRegression()

# Fit model to data
lr.fit(X_train, y_train)

In [ ]:
# Evaluate score of model
train_score = lr.score(X_train, y_train)
test_score = lr.score(X_test, y_test)
print('Linear Regression Train Score:', train_score)
print('Linear Regression Test Score:', test_score)

### Assessment of Feature Dimensions:
- Random Forest Classifier: Random Forest is one of the most widely used algorithms for feature selection in order to help select a smaller subset of features.

In [29]:
# Import relevent classifiers
from sklearn.ensemble import RandomForestRegressor

In [ ]:
# Fit train data to a random forest regressor instance
# a max depth of 20 (arbitraty initial choice)
# same random state as previous models used
# default n_estimators of 100
rfr_model = RandomForestRegressor(random_state=42, n_estimators=100)
rfr_model.fit(X_train, y_train)

### Create a Pipeline

In [28]:
revenue_prediction_pipeline = Pipeline([
    
        # Streamline Preprocessing 
        ('union', FeatureUnion(
            
            transformer_list = [
                
                # Pipeline and Functions for Numerical Data
                ('numeric_features', Pipeline(
                    [
                    ('selector', select_numeric_data),
                    ('imputer', SimpleImputer())
                    ]
                )),
                
                # Pipeline and Functions for Categorical Data
                ('text_features', Pipeline(
                    [
                    ('selector',  select_text_data),
                    # Reduce potential dimensionality from CounterVectorizer by creating hashes instead
                    ('vectorizer', CountVectorizer()),
                    # chi-squared test to select the K features
                    ('dim_red', SelectKBest())
                    ]
                ))
             ]
        )),
        #('scale', StandardScaler()),
        ('rfr', RandomForestRegressor())
    ])

In [29]:
parameters = [
    {'rfr' : [ 
        RandomForestRegressor(
            random_state=42, max_depth=5, n_estimators=100)
    ]},
    {'vectorizer' : [ 
        CountVectorizer(
            stop_words='english')
    ]},
    {'dim_red': [SelectKBest(chi2, k=chi_k)]}
]

In [ ]:
non_negative=True, norm=None, binary=False, ngram_range=(1, 2)

In [30]:
# Create the grid search object
pipeline_cv = GridSearchCV(estimator=revenue_prediction_pipeline,
                  param_grid=parameters,
                  refit=True,
                  cv=5, 
                  n_jobs=-1,
                  verbose=0,
                  scoring='neg_mean_absolute_error')

In [33]:
X_train.shape, y_train.shape

((3253, 11), (3253,))

In [ ]:
# Seed the random number generator
np.random.seed(42)

# Fit pipeline_cv to the training data
grid_result = pipeline_cv.fit(X_train, y_train)

In [ ]:
best_params = grid_result.best_params_

#### Make Predictions

In [85]:
# Import necessary modules
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from math import sqrt

In [86]:
# Calculate the mean squared and absolute errors -TRAIN-
rf_mean_squ_error = mean_squared_error(y_train, rfr_model.predict(X_train_scaled))
rf_mean_abs_error = mean_absolute_error(y_train, rfr_model.predict(X_train_scaled))
print("Random Forest training mse = ", round(rf_mean_squ_error, 2)," & mae = ", round(rf_mean_abs_error, 2)," & rmse = ", round(sqrt(rf_mean_squ_error),2))

Random Forest training mse =  8256618746077463.0  & mae =  56371101.06  & rmse =  90865938.32


The *mean absolute error* (mae) means that **training revenue predictions** were perfect for the decision tree model but on average *$56,371,101.06* away from the true prediction with the random forest model. *Mean squared error*, and consequently root mean squared error (RMSE), results in predictions further and further from the true value are punished more.

In [87]:
# Calculate the mean squared and absolute errors -TEST-
rf_test_mean_squ_error = mean_squared_error(y_test, rfr_model.predict(X_test_scaled))
rf_test_mean_abs_error = mean_absolute_error(y_test, rfr_model.predict(X_test_scaled))
print("Random Forest testing mse = ", round(rf_test_mean_squ_error, 2)," & mae = ", round(rf_test_mean_abs_error, 2)," & rmse = ", round(sqrt(rf_test_mean_squ_error),2))

Random Forest testing mse =  1.745712058406849e+16  & mae =  76682990.29  & rmse =  132125397.2


The *mean absolute error* (mae) means that **testing revenue predictions** were perfect for the decision tree model but on average *$76,682,990.29* away from the true prediction with the random forest model. *Mean squared error*, and consequently root mean squared error (RMSE), results in predictions further and further from the true value are punished more.

#### Visualize Tree

In [88]:
# Import necessary modules
from sklearn.tree import export_graphviz
from IPython.display import Image
import pydot

In [89]:
# Extract the small tree
tree_small = rfr_model.estimators_[5]

# Save the tree as a png image
export_graphviz(tree_small, out_file = 'small_tree.dot', feature_names=feature_list, rounded=True, precision=1)
(graph, ) = pydot.graph_from_dot_file('small_tree.dot')

In [90]:
# Write graph to a png file
Image(graph.create_png())

*Observations*: Clearly, this is a multifacetted issue, and there is far too much feature dimension to create a usable, predictive model for movie revenue. The next step is to create a pipeline using Principle Component Analysis in order to reduce the dimensionality of this data.

In [ ]:
# Measure the accuracy
accuracy = clf.score(____, ____)
print("The accuracy of the classifier on the test set is %.3f" % accuracy)